1. Filter image
2. Random 100,000 points
3. Plotly
4. Filter image
5. Histogram Equalization
6. 100,000 points
7. Plotly

In [2]:
import os

In [3]:
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
from ndreg import *
import ndio.remote.neurodata as neurodata
import nibabel as nb

In [4]:
refToken = "ara_ccf2"
refImg = imgDownload(refToken)

In [5]:
refAnnoImg = imgDownload(refToken, channel="annotation")

In [6]:
randValues = np.random.rand(1000,3)
randValues = np.concatenate(([[0,0,0]],randValues))
randCmap = matplotlib.colors.ListedColormap (randValues)

In [7]:
inToken = "Aut1367"
nd = neurodata()

inImg = imgDownload(inToken, resolution=5)

In [8]:
rawestImg = sitk.GetArrayFromImage(inImg)  ##convert to simpleITK image to normal numpy ndarray

In [9]:
print rawestImg.shape

(1225, 912, 595)


## Rawest Plot (100k sampling)

In [10]:
rawestImg = sitk.GetArrayFromImage(inImg)  ##convert to simpleITK image to normal numpy ndarray

In [27]:
## Randomly sample 100k points
import random
x = rawestImg[:,0,0]
y = rawestImg[0,:,0]
z = rawestImg[0,0,:]

# mod by x to get x, mod by y to get y, mod by z to get z

xdimensions = len(x)
ydimensions = len(y)
zdimensions = len(z)
index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

X_val = []
Y_val = []
Z_val = []

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)

xlist = []
ylist = []
zlist = []
for i in range(100000):
    xlist.append(random.sample(xrange(0,xdimensions), 1)[0])
    ylist.append(random.sample(xrange(0,ydimensions), 1)[0])
    zlist.append(random.sample(xrange(0,zdimensions), 1)[0])
print xlist

[927, 106, 140, 568, 114, 237, 425, 59, 1081, 488, 1043, 1075, 453, 1196, 210, 697, 1104, 11, 699, 989, 270, 738, 133, 439, 403, 589, 223, 474, 43, 969, 75, 245, 583, 171, 1168, 53, 1040, 59, 503, 1009, 129, 692, 1186, 750, 236, 167, 751, 246, 706, 559, 1018, 1089, 914, 106, 924, 404, 358, 132, 911, 493, 603, 714, 933, 275, 886, 1003, 165, 873, 1135, 639, 703, 764, 669, 780, 1162, 1112, 943, 490, 1140, 996, 1080, 100, 153, 637, 682, 255, 491, 862, 518, 518, 474, 128, 793, 688, 1097, 1092, 720, 108, 271, 1100, 506, 613, 1034, 253, 660, 283, 1190, 171, 637, 516, 1211, 324, 585, 762, 791, 425, 1192, 597, 7, 1154, 1224, 125, 615, 170, 393, 164, 914, 251, 675, 39, 374, 545, 471, 1060, 554, 343, 710, 209, 915, 1201, 837, 891, 387, 599, 933, 468, 964, 376, 41, 1143, 673, 619, 979, 318, 655, 156, 174, 4, 665, 669, 201, 914, 1219, 939, 1020, 345, 296, 365, 481, 1112, 854, 481, 941, 480, 18, 141, 960, 210, 1028, 1118, 807, 730, 852, 1090, 443, 634, 744, 1028, 1090, 83, 905, 669, 742, 394, 1023, 

In [28]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly import tools
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go

# x = X_val
# y = Y_val
# z = Z_val
x = xlist
y = ylist
z = zlist

trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367rawest' + "plotly")
plotly.offline.plot(fig, filename= 'AUT1367rawestluke' + "plotly.html")

Aut1367rawestplotly


'file:///home/tony/AUT1367rawestlukeplotly.html'

## Filter image

In [29]:
## Clean out noise (Filter Image)

(values, bins) = np.histogram(sitk.GetArrayFromImage(inImg), bins=100, range=(0,500))
plt.plot(bins[:-1], values)

counts = np.bincount(values)
maximum = np.argmax(counts)

lowerThreshold = 100 #maximum
upperThreshold = sitk.GetArrayFromImage(inImg).max()+1

inImg = sitk.Threshold(inImg,lowerThreshold,upperThreshold,lowerThreshold) - lowerThreshold

## Randomly sample 100k points

In [30]:
filterImg = sitk.GetArrayFromImage(inImg)  ##convert to simpleITK image to normal numpy ndarray

In [31]:
print filterImg[0][0]

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 

In [33]:
## Randomly sample 100k points after filtering
x = filterImg[:,0,0]
y = filterImg[0,:,0]
z = filterImg[0,0,:]

# mod by x to get x, mod by y to get y, mod by z to get z

xdimensions = len(x)
ydimensions = len(y)
zdimensions = len(z)
index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

X_val = []
Y_val = []
Z_val = []

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)

xlist = []
ylist = []
zlist = []
for i in range(100000):
    xlist.append(random.sample(xrange(0,xdimensions), 1)[0])
    ylist.append(random.sample(xrange(0,ydimensions), 1)[0])
    zlist.append(random.sample(xrange(0,zdimensions), 1)[0])
print xlist

[465, 400, 990, 826, 153, 550, 1128, 1091, 344, 304, 448, 226, 753, 694, 856, 103, 689, 820, 154, 362, 717, 806, 667, 900, 614, 1109, 912, 1162, 98, 732, 673, 1198, 1100, 620, 30, 597, 82, 176, 456, 791, 341, 804, 1003, 154, 439, 787, 266, 214, 251, 958, 338, 1003, 153, 119, 650, 74, 1044, 315, 821, 56, 617, 1209, 253, 508, 200, 951, 18, 477, 1172, 73, 465, 132, 1053, 523, 68, 954, 1057, 265, 99, 810, 17, 485, 89, 1148, 224, 1221, 956, 542, 270, 1099, 747, 145, 475, 519, 410, 804, 626, 513, 733, 761, 922, 768, 359, 826, 649, 43, 904, 1031, 180, 908, 855, 386, 130, 48, 1045, 569, 202, 361, 730, 288, 536, 959, 252, 984, 1029, 18, 128, 156, 360, 978, 53, 84, 1036, 718, 755, 625, 351, 322, 209, 1065, 206, 938, 796, 957, 952, 749, 58, 28, 1004, 453, 510, 888, 171, 780, 490, 816, 123, 273, 342, 821, 86, 1057, 687, 579, 910, 1215, 452, 644, 155, 471, 372, 831, 384, 682, 1157, 772, 339, 789, 64, 859, 848, 881, 1083, 250, 1063, 677, 329, 1099, 293, 764, 562, 541, 69, 485, 268, 524, 833, 413, 21

In [34]:
print X_val
print Y_val
print Z_val

print len(X_val)
print len(Y_val)
print len(Z_val)

[650, 853, 492, 719, 1158, 94, 279, 184, 327, 1029, 517, 74, 1078, 122, 75, 516, 1193, 345, 628, 981, 1147, 734, 414, 1184, 23, 871, 1155, 951, 361, 478, 873, 704, 675, 92, 914, 1103, 257, 159, 358, 1224, 914, 678, 95, 535, 1221, 1199, 1118, 920, 1067, 1204, 589, 564, 774, 684, 395, 154, 1151, 676, 1141, 927, 549, 526, 67, 591, 712, 1126, 270, 732, 736, 555, 721, 336, 894, 1159, 1117, 1003, 999, 842, 1222, 1068, 927, 1147, 722, 11, 1196, 272, 919, 1070, 347, 701, 721, 635, 1021, 578, 528, 508, 947, 619, 599, 1073, 941, 38, 434, 912, 1001, 881, 144, 506, 788, 793, 613, 63, 357, 147, 1179, 253, 229, 1062, 1020, 679, 488, 727, 1215, 680, 372, 579, 262, 832, 536, 284, 993, 282, 895, 876, 662, 151, 1199, 992, 173, 237, 73, 738, 1116, 1200, 1201, 570, 1146, 913, 887, 1176, 32, 1166, 686, 81, 302, 229, 521, 130, 204, 706, 222, 508, 1006, 304, 33, 852, 393, 1113, 7, 1167, 543, 141, 181, 392, 516, 1191, 229, 822, 1023, 837, 515, 29, 1140, 1194, 1161, 900, 1005, 799, 208, 271, 390, 521, 125, 363

UNUSED:  
spacingImg = inImg.GetSpacing()  
spacing = tuple(i * 50 for i in spacingImg)  
print spacingImg  
print spacing  
inImg.SetSpacing(spacingImg)  
inImg_download = inImg  # Aut1367 set to default spacing  
inImg = imgResample(inImg, spacing=refImg.GetSpacing())  
Img_reorient = imgReorient(inImg, "LPS", "RSA") #specific reoriented Aut1367  
inImg_reorient = Img_reorient  
refImg_ds = imgResample(refImg, spacing=spacing)   # atlas downsample 50x

## Plot of 100k data post filtering

In [35]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly import tools
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go

x = X_val
y = Y_val
z = Z_val

trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367filter' + "plotly")
plotly.offline.plot(fig, filename= 'AUT1367filter' + "plotly.html")

Aut1367filterplotly


'file:///home/tony/AUT1367filterplotly.html'

## Filter Image Again
Don't do this

## Clean out noise (Filter Image)

(values, bins) = np.histogram(filterImg, bins=100, range=(0,500))
plt.plot(bins[:-1], values)

counts = np.bincount(values)
maximum = np.argmax(counts)

lowerThreshold = maximum
upperThreshold = filterImg.max()+1

filterX2Img = sitk.Threshold(inImg,lowerThreshold,upperThreshold,lowerThreshold) - lowerThreshold

newImg = sitk.GetArrayFromImage(filterX2Img)  ##convert to simpleITK image to normal numpy ndarray

In [36]:
## Histogram Equalization
## Cut from generateHistogram from clarityviz
import cv2
im = filterImg
img = im[:,:,:]
shape = im.shape
#affine = im.get_affine()
x_value = shape[0]
y_value = shape[1]
z_value = shape[2]
#####################################################
imgflat = img.reshape(-1)
#img_grey = np.array(imgflat * 255, dtype = np.uint8)
#img_eq = exposure.equalize_hist(img_grey)#new_img = img_eq.reshape(x_value, y_value, z_value)
#globaleq = nib.Nifti1Image(new_img, np.eye(4))
    
#nb.save(globaleq, '/home/albert/Thumbo/AutAglobaleq.nii')
######################################################
#clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8,8))
clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8,8))
img_grey = np.array(imgflat * 255, dtype = np.uint8)
#threshed = cv2.adaptiveThreshold(img_grey, 255, cv2.ADAPTIVE_THRESH_MEAN_C, cv2.THRESH_BINARY, 3, 0)
cl1 = clahe.apply(img_grey)
#cv2.imwrite('clahe_2.jpg',cl1)
#cv2.startWindowThread()
#cv2.namedWindow("adaptive")
#cv2.imshow("adaptive", cl1)
#cv2.imshow("adaptive", threshed)
#plt.imshow(threshed)
localimgflat = cl1 #cl1.reshape(-1)
newer_img = localimgflat.reshape(x_value, y_value, z_value)  ##this is the numpy.ndarray version
localeq = nb.Nifti1Image(newer_img, np.eye(4))

In [37]:
print newer_img.shape

(1225, 912, 595)


## Plotting post filtering/HistEq

In [39]:
x_histeq = newer_img[:,0,0]
y_histeq = newer_img[0,:,0]
z_histeq = newer_img[0,0,:]

## Randomly sample 100k points after filtering

xdimensions = len(x)
ydimensions = len(y)
zdimensions = len(z)
index = random.sample(xrange(0,xdimensions*ydimensions*zdimensions),100000)  #66473400 is multiplying xshape by yshape by zshape

X_val = []
Y_val = []
Z_val = []

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)

xlist = []
ylist = []
zlist = []

for i in range(100000):
    xlist.append(random.sample(xrange(0,xdimensions), 1)[0])
    ylist.append(random.sample(xrange(0,ydimensions), 1)[0])
    zlist.append(random.sample(xrange(0,zdimensions), 1)[0])

for i in index:
    z_val = int(i/(xdimensions*ydimensions))
    z_rem = i%(xdimensions*ydimensions)
    y_val = int(z_rem/xdimensions)
    x_val = int(z_rem/ydimensions)
    
    X_val.append(x_val)
    Y_val.append(y_val)
    Z_val.append(z_val)
    
trace1 = go.Scatter3d(
    x = x,
    y = y,
    z = z,
    mode='markers',
    marker=dict(
        size=1.2,
        color='purple',                # set color to an array/list of desired values
        colorscale='Viridis',          # choose a colorscale
        opacity=0.15
    )
)
data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)

fig = go.Figure(data=data, layout=layout)
print('Aut1367postfilterHistEq' + "plotly")
plotly.offline.plot(fig, filename= 'Aut1367postfilterHistEq' + "plotly.html")

Aut1367postfilterHistEqplotly


'file:///home/tony/Aut1367postfilterHistEqplotly.html'